In [1]:
import pandas as pd

data = {
    "text": [
        "I love this movie!",
        "This is the best phone I've ever used.",
        "The food was amazing and the service was great.",
        "This product is okay, not the best though.",
        "It's fine, but I expected more.",
        "The movie was boring and too long.",
        "I hate this restaurant, terrible experience.",
        "The laptop stopped working after one week.",
        "Nothing special about this item.",
        "Absolutely fantastic! Highly recommend."
    ],
    "label": [
        "positive",
        "positive",
        "positive",
        "neutral",
        "neutral",
        "negative",
        "negative",
        "negative",
        "neutral",
        "positive"
    ]
}

df = pd.DataFrame(data)
df.to_csv("/content/data.csv", index=False)
print("✅ Đã tạo file /content/data.csv")


✅ Đã tạo file /content/data.csv


In [3]:
# ==============================================
# 1️⃣ CÀI ĐẶT & IMPORT
# ==============================================
!pip install transformers datasets torch scikit-learn -q

from datasets import load_dataset, Dataset
from transformers import AutoTokenizer, AutoModelForSequenceClassification, Trainer, TrainingArguments
from sklearn.model_selection import train_test_split
import pandas as pd
import numpy as np
import torch

# ==============================================
# 2️⃣ NẠP & CHUẨN HÓA DỮ LIỆU
# ==============================================
# Giả sử bạn có file CSV: data.csv gồm 2 cột text, label
data = pd.read_csv("/content/data.csv")

# Chuẩn hóa nhãn (map từ string -> số)
label2id = {label: idx for idx, label in enumerate(data['label'].unique())}
id2label = {v: k for k, v in label2id.items()}
data['label'] = data['label'].map(label2id)

# Chia train/test
train_df, test_df = train_test_split(data, test_size=0.2, random_state=42)
train_dataset = Dataset.from_pandas(train_df)
test_dataset = Dataset.from_pandas(test_df)

# ==============================================
# 3️⃣ TOKENIZATION
# ==============================================
model_name = "bert-base-uncased"  # có thể đổi sang model tiếng Việt: "vinai/phobert-base"
tokenizer = AutoTokenizer.from_pretrained(model_name)

def tokenize_fn(batch):
    return tokenizer(batch["text"], padding="max_length", truncation=True, max_length=128)

train_dataset = train_dataset.map(tokenize_fn, batched=True)
test_dataset = test_dataset.map(tokenize_fn, batched=True)

# Xóa cột không cần
train_dataset = train_dataset.remove_columns(["text", "__index_level_0__"])
test_dataset = test_dataset.remove_columns(["text", "__index_level_0__"])

train_dataset.set_format("torch")
test_dataset.set_format("torch")

# ==============================================
# 4️⃣ CHỌN MÔ HÌNH
# ==============================================
model = AutoModelForSequenceClassification.from_pretrained(
    model_name,
    num_labels=len(label2id),
    id2label=id2label,
    label2id=label2id
)



Map:   0%|          | 0/8 [00:00<?, ? examples/s]

Map:   0%|          | 0/2 [00:00<?, ? examples/s]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [6]:
# ==============================================
import os
os.environ["WANDB_DISABLED"] = "true"

# 5️⃣ HUẤN LUYỆN
# ==============================================
training_args = TrainingArguments(
    output_dir="./results",
    learning_rate=2e-5,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=2,
    logging_dir="./logs",
    logging_steps=10,
)



from sklearn.metrics import accuracy_score, precision_recall_fscore_support

def compute_metrics(eval_pred):
    logits, labels = eval_pred
    preds = np.argmax(logits, axis=-1)
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='weighted')
    acc = accuracy_score(labels, preds)
    return {"accuracy": acc, "precision": precision, "recall": recall, "f1": f1}

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

trainer.train()

# ==============================================
# 6️⃣ ĐÁNH GIÁ
# ==============================================
metrics = trainer.evaluate()
print(metrics)

# ==============================================
# 7️⃣ TRIỂN KHAI DỰ ĐOÁN
# ==============================================
def predict(text):
    inputs = tokenizer(text, return_tensors="pt", truncation=True, padding=True, max_length=128)
    with torch.no_grad():
        outputs = model(**inputs)
        probs = torch.nn.functional.softmax(outputs.logits, dim=-1)
        pred = torch.argmax(probs, dim=-1).item()
    return id2label[pred], probs[0][pred].item()

print(predict("I really love this product!"))
print(predict("This is the worst thing ever."))

Using the `WANDB_DISABLED` environment variable is deprecated and will be removed in v5. Use the --report_to flag to control the integrations used for logging result (for instance --report_to none).
/tmp/ipython-input-824382958.py:28: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
/usr/local/lib/python3.12/dist-packages/torch/utils/data/dataloader.py:666: UserWarning: 'pin_memory' argument is set as true but no accelerator is found, then device pinned memory won't be used.
  warnings.warn(warn_msg)


/usr/local/lib/python3.12/dist-packages/torch/utils/data/dataloader.py:666: UserWarning: 'pin_memory' argument is set as true but no accelerator is found, then device pinned memory won't be used.
  warnings.warn(warn_msg)


/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


{'eval_loss': 1.0297198295593262, 'eval_accuracy': 0.5, 'eval_precision': 0.25, 'eval_recall': 0.5, 'eval_f1': 0.3333333333333333, 'eval_runtime': 1.4353, 'eval_samples_per_second': 1.393, 'eval_steps_per_second': 0.697, 'epoch': 2.0}
('positive', 0.44261372089385986)
('positive', 0.41787630319595337)


#Model HG

In [ ]:
# ==========================================
# 🧩 CÀI ĐẶT THƯ VIỆN
# ==========================================
!pip install -q huggingface_hub

# ==========================================
# ⚙️ IMPORT CÁC MODULE CẦN THIẾT
# ==========================================
from huggingface_hub import snapshot_download

# ==========================================
# 🧠 NHẬP TÊN MODEL MUỐN TẢI
# ==========================================
# 👉 Ví dụ: Stable Diffusion XL base 1.0
model_id = "stabilityai/stable-diffusion-xl-base-1.0"

# Nếu bạn muốn thay model khác, chỉ cần đổi model_id
# Ví dụ:
# model_id = "bert-base-uncased"
# model_id = "facebook/bart-large-cnn"
# model_id = "openai/whisper-small"

# ==========================================
# 📦 TẢI MODEL VỀ MÁY (KHÔNG CẦN ĐĂNG NHẬP)
# ==========================================
model_path = snapshot_download(
    repo_id=model_id,
    local_dir="models/" + model_id.split("/")[-1],  # lưu vào thư mục models/
    revision="main",  # nhánh chính
    token=None        # KHÔNG cần token
)

# ==========================================
# ✅ IN RA ĐƯỜNG DẪN MODEL SAU KHI TẢI
# ==========================================
print(f"✅ Model '{model_id}' đã được tải về tại: {model_path}")


In [ ]:
model_id = "bert-base-uncased"
snapshot_download(repo_id=model_id, local_dir=f"/kaggle/working/{model_id.split('/')[-1]}")
tokenizer = AutoTokenizer.from_pretrained(f"/kaggle/working/{model_id.split('/')[-1]}")
model = AutoModel.from_pretrained(f"/kaggle/working/{model_id.split('/')[-1]}")

inputs = tokenizer("This is a test sentence.", return_tensors="pt")
outputs = model(**inputs)
print(outputs.last_hidden_state.shape)

# Kaggle

In [ ]:
# ============================================================
# ⚙️ 1️⃣ CÀI ĐẶT THƯ VIỆN CẦN THIẾT
# ============================================================
# diffusers: dùng cho model Stable Diffusion, T2I, SDXL,...
# transformers: cho NLP, vision-language models
# accelerate + safetensors: giúp tăng tốc & load file an toàn
# huggingface_hub: thao tác tải & quản lý model từ Hugging Face
# ============================================================
!pip install -U diffusers transformers accelerate safetensors huggingface_hub torch torchvision xformers --quiet


# ============================================================
# 🔑 2️⃣ ĐĂNG NHẬP HUGGING FACE
# ============================================================
# - Cần token để tải model private hoặc có license.
# - Lấy token tại: https://huggingface.co/settings/tokens
# ============================================================
from huggingface_hub import login

login()  # 👉 Chạy lệnh này rồi dán token Hugging Face vào ô nhập


# ============================================================
# 🧠 3️⃣ NHẬP TÊN MODEL MUỐN TẢI
# ============================================================
# - Bạn có thể thay "model_id" bằng bất kỳ model nào:
#   📚 NLP: "bert-base-uncased", "vinai/phobert-base-v2"
#   🖼️ T2I: "stabilityai/stable-diffusion-xl-base-1.0"
#   🎧 Audio: "facebook/wav2vec2-base-960h"
# ============================================================

model_id = "stabilityai/stable-diffusion-xl-base-1.0"  # 👉 đổi tên model ở đây


# ============================================================
# 💾 4️⃣ TẢI MODEL VỀ THƯ MỤC LÀM VIỆC (VD: /kaggle/working/)
# ============================================================
# - Model sẽ được lưu vào /kaggle/working/<model_id> để dùng lại.
# - Nếu muốn lưu trên Google Drive hoặc Dataset riêng thì chỉ cần đổi đường dẫn.
# ============================================================

from huggingface_hub import snapshot_download

# Tải toàn bộ model (bao gồm weights, config, tokenizer,...)
local_dir = f"/kaggle/working/{model_id.split('/')[-1]}"
snapshot_download(repo_id=model_id, local_dir=local_dir, resume_download=True)

print(f"✅ Model đã tải về thư mục: {local_dir}")


# ============================================================
# 🧪 5️⃣ LOAD MODEL ĐỂ DÙNG (THEO LOẠI)
# ============================================================

from transformers import AutoModel, AutoTokenizer
from diffusers import StableDiffusionXLPipeline
import torch

# 👉 Kiểm tra loại model để load đúng lớp
if "diffusion" in model_id.lower() or "sdxl" in model_id.lower():
    print("🖼️ Đây là model diffusion, dùng pipeline SDXL...")
    pipe = StableDiffusionXLPipeline.from_pretrained(
        local_dir,
        torch_dtype=torch.float16,
        use_safetensors=True,
        variant="fp16"
    ).to("cuda")

    prompt = "a cute cat wearing glasses, watercolor style"
    image = pipe(prompt).images[0]
    image.save("/kaggle/working/sample.png")
    print("✅ Đã tạo ảnh mẫu: /kaggle/working/sample.png")

else:
    print("📚 Đây là model NLP/Transformer thông thường...")
    tokenizer = AutoTokenizer.from_pretrained(local_dir)
    model = AutoModel.from_pretrained(local_dir)

    # Ví dụ: mã hóa câu
    inputs = tokenizer("Hello Hugging Face!", return_tensors="pt")
    with torch.no_grad():
        outputs = model(**inputs)
    print("✅ Đã load thành công model NLP, vector đầu ra:", outputs.last_hidden_state.shape)


# ============================================================
# 🧰 6️⃣ (TUỲ CHỌN) LƯU MODEL LÊN DRIVE HOẶC DATASET
# ============================================================
# Nếu bạn muốn lưu lại model để dùng sau:
# ============================================================
# !cp -r /kaggle/working/<model_folder> /kaggle/drive/MyDrive/

#Exam

In [ ]:
!pip install -U diffusers transformers accelerate safetensors torch torchvision xformers --quiet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.1/4.1 MB 37.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 899.7/899.7 MB 1.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 594.3/594.3 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.2/10.2 MB 58.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.0/88.0 MB 9.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 954.8/954.8 kB 24.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.1/193.1 MB 6.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 24.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 63.6/63.6 MB 12.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 267.5/267.5 MB 4.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 288.2/288.2 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 322.3/322.3 MB 4.9 MB/s eta 0:00:00
   ━━━

In [ ]:
from diffusers import StableDiffusionXLPipeline
import torch

model_id = "stabilityai/stable-diffusion-xl-base-1.0"

pipe = StableDiffusionXLPipeline.from_pretrained(
    model_id,
    torch_dtype=torch.float16,
    use_safetensors=True,
    variant="fp16"
).to("cuda")


In [ ]:
prompt = "A cute cat sitting on a pile of books, watercolor style"
image = pipe(prompt).images[0]
image.save("sample.png")

image
